In [240]:
import pandas as pd
import geopandas as gp
import numpy as np
import censusgeocode as cg
import time
import os
import json

In [68]:
census_tracts = gp.read_file('/Users/ameliabaum/Desktop/Amelia/Berkeley 2018-2019/EnRes C190/evictionmodel_190final/data/cb_2017_06_tract_500k/cb_2017_06_tract_500k.shp')
sf_tracts = census_tracts[census_tracts['COUNTYFP'] == '075']
sf_tracts.head() #196 census tracts in SF

STATEFP COUNTYFP TRACTCE              AFFGEOID        GEOID    NAME LSAD  \
430      06      075  010200  1400000US06075010200  06075010200     102   CT   
431      06      075  011200  1400000US06075011200  06075011200     112   CT   
432      06      075  012401  1400000US06075012401  06075012401  124.01   CT   
433      06      075  013300  1400000US06075013300  06075013300     133   CT   
434      06      075  015900  1400000US06075015900  06075015900     159   CT   

      ALAND  AWATER                                           geometry  
430  515959  295388  POLYGON ((-122.426671 37.809639, -122.424876 3...  
431  177415       0  POLYGON ((-122.416292 37.793892, -122.415218 3...  
432   91972       0  POLYGON ((-122.417707 37.784236, -122.416072 3...  
433  581310       0  POLYGON ((-122.459476 37.789711, -122.45274 37...  
434  296386       0  POLYGON ((-122.434562 37.784152, -122.431291 3...

In [246]:
#get evictions data from 2009 to find the number in neighbors from the last 2 years
sf_evictions = pd.read_csv("/Users/ameliabaum/Desktop/Amelia/Berkeley 2018-2019/EnRes C190/evictionmodel_190final/data/Eviction_Notices.csv")
sf_evictions["Year"] = sf_evictions["File Date"].astype(str).apply(lambda row: row[6:])
sf_evictions["Year"] = sf_evictions["Year"].astype(int)
sf_evictions_09 = sf_evictions[sf_evictions["Year"] >= 2009].dropna()
sf_evictions_09 = sf_evictions_09.replace({False:0, True: 1})
#split lat and lon into different cols to be geocoded
sf_evictions_09["Latitude"] = sf_evictions_09["Location"].astype(str).apply(lambda row: row.split(",")[0][1:])
sf_evictions_09["Longitude"] = sf_evictions_09["Location"].astype(str).apply(lambda row: row.split(",")[1][:-1])

sf_evictions_09.head()

/Users/ameliabaum/anaconda3/lib/python3.7/site-packages/IPython/core/interactiveshell.py:2785: DtypeWarning: Columns (4) have mixed types. Specify dtype option on import or set low_memory=False.
  interactivity=interactivity, compiler=compiler, result=result)


Eviction ID                         Address           City State  \
6      M172623    100 Block Of Charles  Street  San Francisco    CA   
10     M172628  1300 Block Of Chestnut  Street  San Francisco    CA   
14     M172503      1200 Block Of 41st  Avenue  San Francisco    CA   
22     M172511          0 Block Of 5th  Avenue  San Francisco    CA   
25     M172709   100 Block Of Prospect  Avenue  San Francisco    CA   

   Eviction Notice Source Zipcode   File Date  Non Payment  Breach  Nuisance  \
6                           94131  10/19/2017            0       0         0   
10                          94123  10/23/2017            0       0         0   
14                          94122  10/02/2017            0       0         0   
22                          94118  10/10/2017            0       0         0   
25                          94110  10/26/2017            0       0         0   

    Illegal Use          ...           Lead Remediation  Development  \
6             0          ...                          0            0   
10            0          ...                          0            0   
14            0          ...                          0            0   
22            0          ...                          0            0   
25            0          ...                          0            0   

    Good Samaritan Ends  Constraints Date  Supervisor District  \
6                     0        12/17/2022                  8.0   
10                    0        12/17/2022                  2.0   
14                    0        11/29/2022                  4.0   
22                    0        12/05/2022                  2.0   
25                    0        12/24/2022                  9.0   

    Neighborhoods - Analysis Boundaries  \
6                             Glen Park   
10                               Marina   
14                      Sunset/Parkside   
22                       Inner Richmond   
25                       Bernal Heights   

                                     Location  Year            Latitude  \
6    (37.738336951880164, -122.4256608010048)  2017  37.738336951880164   
10   (37.80223066530217, -122.42556524759928)  2017   37.80223066530217   
14   (37.76346716977734, -122.50069529991866)  2017   37.76346716977734   
22  (37.787705866671075, -122.46361972068956)  2017  37.787705866671075   
25   (37.74296049255459, -122.41894065545237)  2017   37.74296049255459   

               Longitude  
6     -122.4256608010048  
10   -122.42556524759928  
14   -122.50069529991866  
22   -122.46361972068956  
25   -122.41894065545237  

[5 rows x 32 columns]

In [247]:
def getGeoid(lon, lat):
#pings the FCC API to geocode lat lon coordinates to other geograpies. Returns a 2 item array of [geoid, tract name]
    try:
        result = cg.coordinates(lon, lat)
        geoid = result['Census Tracts'][0]['GEOID']
        return geoid
    except(ValueError, TypeError):
        return 'Nan'

In [251]:
start = time.time()
sf_evictions_09["Geoid"] = sf_evictions_09.apply(lambda row: getGeoid(row["Longitude"], row["Latitude"]), axis=1)
end = time.time()
elapsed = end-start #this takes like ~30 mins

In [252]:
elapsed

2368.6420459747314

In [253]:
sf_evictions_09["geoid_year"] = sf_evictions_09["Geoid"].astype(str) + sf_evictions_09["Year"].astype(str)
sf_evictions_09.head()

Eviction ID                         Address           City State  \
6      M172623    100 Block Of Charles  Street  San Francisco    CA   
10     M172628  1300 Block Of Chestnut  Street  San Francisco    CA   
14     M172503      1200 Block Of 41st  Avenue  San Francisco    CA   
22     M172511          0 Block Of 5th  Avenue  San Francisco    CA   
25     M172709   100 Block Of Prospect  Avenue  San Francisco    CA   

   Eviction Notice Source Zipcode   File Date  Non Payment  Breach  Nuisance  \
6                           94131  10/19/2017            0       0         0   
10                          94123  10/23/2017            0       0         0   
14                          94122  10/02/2017            0       0         0   
22                          94118  10/10/2017            0       0         0   
25                          94110  10/26/2017            0       0         0   

    Illegal Use       ...         Good Samaritan Ends  Constraints Date  \
6             0       ...                           0        12/17/2022   
10            0       ...                           0        12/17/2022   
14            0       ...                           0        11/29/2022   
22            0       ...                           0        12/05/2022   
25            0       ...                           0        12/24/2022   

    Supervisor District  Neighborhoods - Analysis Boundaries  \
6                   8.0                            Glen Park   
10                  2.0                               Marina   
14                  4.0                      Sunset/Parkside   
22                  2.0                       Inner Richmond   
25                  9.0                       Bernal Heights   

                                     Location  Year            Latitude  \
6    (37.738336951880164, -122.4256608010048)  2017  37.738336951880164   
10   (37.80223066530217, -122.42556524759928)  2017   37.80223066530217   
14   (37.76346716977734, -122.50069529991866)  2017   37.76346716977734   
22  (37.787705866671075, -122.46361972068956)  2017  37.787705866671075   
25   (37.74296049255459, -122.41894065545237)  2017   37.74296049255459   

               Longitude        Geoid       geoid_year  
6     -122.4256608010048  06075021800  060750218002017  
10   -122.42556524759928  06075012901  060750129012017  
14   -122.50069529991866  06075035100  060750351002017  
22   -122.46361972068956  06075040100  060750401002017  
25   -122.41894065545237  06075025300  060750253002017  

[5 rows x 34 columns]

In [261]:
evictions_geocoded09_tractandyear = sf_evictions_09.groupby(["Geoid", "Year"]).count()
evictions_geocoded09_tractandyear.head()
# evictions_geocoded09_tractandyear.drop(["Neighborhoods - Analysis Boundaries", "Location", "Latitude", "Longitude", 
#         "Eviction Notice Source Zipcode", "Address", "City", "State", "Constraints Date", "File Date", "Supervisor District"], axis=1) #166 census tracts represented

Eviction ID  Address  City  State  \
Geoid       Year                                      
06075010100 2009            1        1     1      1   
            2011            2        2     2      2   
06075010200 2012            1        1     1      1   
            2017            1        1     1      1   
06075010300 2010            2        2     2      2   

                  Eviction Notice Source Zipcode  File Date  Non Payment  \
Geoid       Year                                                           
06075010100 2009                               1          1            1   
            2011                               2          2            2   
06075010200 2012                               1          1            1   
            2017                               1          1            1   
06075010300 2010                               2          2            2   

                  Breach  Nuisance  Illegal Use     ...      Lead Remediation  \
Geoid       Year                                    ...                         
06075010100 2009       1         1            1     ...                     1   
            2011       2         2            2     ...                     2   
06075010200 2012       1         1            1     ...                     1   
            2017       1         1            1     ...                     1   
06075010300 2010       2         2            2     ...                     2   

                  Development  Good Samaritan Ends  Constraints Date  \
Geoid       Year                                                       
06075010100 2009            1                    1                 1   
            2011            2                    2                 2   
06075010200 2012            1                    1                 1   
            2017            1                    1                 1   
06075010300 2010            2                    2                 2   

                  Supervisor District  Neighborhoods - Analysis Boundaries  \
Geoid       Year                                                             
06075010100 2009                    1                                    1   
            2011                    2                                    2   
06075010200 2012                    1                                    1   
            2017                    1                                    1   
06075010300 2010                    2                                    2   

                  Location  Latitude  Longitude  geoid_year  
Geoid       Year                                             
06075010100 2009         1         1          1           1  
            2011         2         2          2           2  
06075010200 2012         1         1          1           1  
            2017         1         1          1           1  
06075010300 2010         2         2          2           2  

[5 rows x 32 columns]

In [262]:
evictions_geocoded09_tractandyear.to_csv("data/evictions_geocoded09_tractandyear.csv")

In [269]:
# evictions = pd.read_csv("data/evictions_geocoded11_tractandyear.csv")
evictions_geocoded09_tractandyear["Total"] = evictions_geocoded09_tractandyear["Non Payment"]
#evictions_geocoded09_tractandyear.columns
# evictions_geocoded09_tractandyear = evictions_geocoded09_tractandyear.drop(['Non Payment', 'Breach',
#        'Nuisance', 'Illegal Use', 'Failure to Sign Renewal', 'Access Denial',
#        'Unapproved Subtenant', 'Owner Move In', 'Demolition',
#        'Capital Improvement', 'Substantial Rehab', 'Ellis Act WithDrawal',
#        'Condo Conversion', 'Roommate Same Unit', 'Other Cause',
#        'Late Payments', 'Lead Remediation', 'Development',
#        'Good Samaritan Ends', "Supervisor District", "File Date", "Address", "City", "State"], axis=1).dropna()
evictions_geocoded09_tractandyear.head()
# # evictions["geoid_year"] = evictions["Geoid"]+ evictions["Year"] # not needed
# evictions["Geoid"] = evictions["Geoid"].astype(int)
# # evictions.dtypes
#evictions.head()

KeyError: 'Non Payment'

In [196]:
#Takes in a geodataframe of all the census tracts and their associated shape polygons in SF. 
#Builds a dictionary where the keys are each unique tract number and the values are an array of geographic neighbors 
#of that tract.
tract_neighbors_dict = {}
def find_neighbors(geodataframe):
    neighbors_dict = {}
    for df_row in geodataframe.iterrows(): #index, then row
        polygon = df_row[1]["geometry"]
        tract = int(df_row[1]["GEOID"])
        
        tract_neighbors_dict[int(tract)] = list((geodataframe[geodataframe.apply(lambda row: row['geometry'].touches(polygon), axis=1)]["GEOID"].values).astype(int))
        #list so that it is easier to write to json later
         
    return tract_neighbors_dict

In [197]:
neighbors = find_neighbors(sf_tracts)
# with open('data/tract_neighbors.json', 'w') as fp:
#         json.dump(neighbors, fp)



In [274]:
features = pd.read_csv("/Users/ameliabaum/Desktop/Amelia/Berkeley 2018-2019/EnRes C190/evictionmodel_190final/data/clean_demographic_data.csv")
features["geoid_year"] = features["Geoid"].astype(str)+ features["Year"].astype(str)
features.head()

Unnamed: 0       Geoid  num Evictions      geoid_year  Total Population  \
0           0  6075010100              2  60750101002011         3851.0000   
1           1  6075010200              1  60750102002012         4040.0000   
2           2  6075010200              1  60750102002017         4668.5488   
3           3  6075010300              2  60750103002012         4393.0000   
4           4  6075010300              2  60750103002013         4729.0000   

   Total Housing Units  Total; Estimate; Average household size  Year  \
0            2278.0000                                 1.750000  2011   
1            2946.0000                                 1.510000  2012   
2            2044.1584                                 2.504992  2017   
3            2254.0000                                 2.260000  2012   
4            2303.0000                                 2.290000  2013   

   Median Year Structure Built  Median Year Moved In  \
0                  1971.000000           2005.000000   
1                  1939.000000           2005.000000   
2                  1944.264423           2006.528939   
3                  1939.000000           2005.000000   
4                  1939.000000           2007.000000   

   Percent with Bachelor's degree  Median rent burden  Evictions per units  \
0                        34.00000            28.40000             0.000878   
1                        42.10000            22.50000             0.000339   
2                       508.85824            28.24032             0.001267   
3                        31.10000            24.30000             0.000887   
4                        31.30000            26.10000             0.000868   

   Percent Black  Percent White  Percent Asian  Percent Native  Percent H, PI  
0       0.089847       0.437808       0.391327        0.002856       0.000000  
1       0.011139       0.824257       0.087624        0.000000       0.000000  
2       0.043886       0.514993       0.335039        0.003474       0.003172  
3       0.000000       0.648532       0.351468        0.000000       0.000000  
4       0.000000       0.577289       0.401988        0.000000       0.000000

In [288]:
neighbor_evictions_col = []
for name, record in features.iterrows(): #this is a row in the features dataframe    
    record_geoid = record["Geoid"]
    print(record_geoid)
    print(record["geoid_year"])
    record_year = int(record["geoid_year"]) %10000
    print(record_year)
    neighbor_years = [record_year - 1, record_year - 2]
    print('neighbor years:', neighbor_years)
    tract_neighbors = neighbors[record_geoid]
    all_neighbor_evictions = []
    for n in tract_neighbors:
        neighbor_evictions_df = features[(features["Geoid"] == record_geoid) & (features["Year"].isin(neighbor_years))]

#         neighbor_evictions_df = evictions[(evictions["Geoid"] == record_geoid) & (evictions["Year"].isin(neighbor_years))]
        print(neighbor_evictions_df)
        all_neighbor_evictions.append(sum(neighbor_evictions_df["num Evictions"]))
    neighbor_evictions_col.append(np.mean(all_neighbor_evictions))
    print(all_neighbor_evictions)
    

features["Neighbors Mean"] = neighbor_evictions_col
#print(neighbors)

6075010100
60750101002011
2011
neighbor years: [2010, 2009]
Empty DataFrame
Columns: [Unnamed: 0, Geoid, num Evictions, geoid_year, Total Population, Total Housing Units, Total; Estimate; Average household size, Year, Median Year Structure Built, Median Year Moved In, Percent with Bachelor's degree, Median rent burden, Evictions per units, Percent Black, Percent White, Percent Asian, Percent Native, Percent H, PI]
Index: []
Empty DataFrame
Columns: [Unnamed: 0, Geoid, num Evictions, geoid_year, Total Population, Total Housing Units, Total; Estimate; Average household size, Year, Median Year Structure Built, Median Year Moved In, Percent with Bachelor's degree, Median rent burden, Evictions per units, Percent Black, Percent White, Percent Asian, Percent Native, Percent H, PI]
Index: []
Empty DataFrame
Columns: [Unnamed: 0, Geoid, num Evictions, geoid_year, Total Population, Total Housing Units, Total; Estimate; Average household size, Year, Median Year Structure Built, Median Year Moved

Index: []
Empty DataFrame
Columns: [Unnamed: 0, Geoid, num Evictions, geoid_year, Total Population, Total Housing Units, Total; Estimate; Average household size, Year, Median Year Structure Built, Median Year Moved In, Percent with Bachelor's degree, Median rent burden, Evictions per units, Percent Black, Percent White, Percent Asian, Percent Native, Percent H, PI]
Index: []
Empty DataFrame
Columns: [Unnamed: 0, Geoid, num Evictions, geoid_year, Total Population, Total Housing Units, Total; Estimate; Average household size, Year, Median Year Structure Built, Median Year Moved In, Percent with Bachelor's degree, Median rent burden, Evictions per units, Percent Black, Percent White, Percent Asian, Percent Native, Percent H, PI]
Index: []
Empty DataFrame
Columns: [Unnamed: 0, Geoid, num Evictions, geoid_year, Total Population, Total Housing Units, Total; Estimate; Average household size, Year, Median Year Structure Built, Median Year Moved In, Percent with Bachelor's degree, Median rent b

15       0.043886       0.514993       0.335039        0.003474       0.003172  
[7, 7, 7, 7, 7]
6075010600
60750106002013
2013
neighbor years: [2012, 2011]
Empty DataFrame
Columns: [Unnamed: 0, Geoid, num Evictions, geoid_year, Total Population, Total Housing Units, Total; Estimate; Average household size, Year, Median Year Structure Built, Median Year Moved In, Percent with Bachelor's degree, Median rent burden, Evictions per units, Percent Black, Percent White, Percent Asian, Percent Native, Percent H, PI]
Index: []
Empty DataFrame
Columns: [Unnamed: 0, Geoid, num Evictions, geoid_year, Total Population, Total Housing Units, Total; Estimate; Average household size, Year, Median Year Structure Built, Median Year Moved In, Percent with Bachelor's degree, Median rent burden, Evictions per units, Percent Black, Percent White, Percent Asian, Percent Native, Percent H, PI]
Index: []
Empty DataFrame
Columns: [Unnamed: 0, Geoid, num Evictions, geoid_year, Total Population, Total Housing Uni

25       0.015381       0.471835       0.489295        0.004781            0.0  
    Unnamed: 0       Geoid  num Evictions      geoid_year  Total Population  \
24          24  6075010800              1  60750108002011            4819.0   
25          25  6075010800              1  60750108002012            4811.0   

    Total Housing Units  Total; Estimate; Average household size  Year  \
24               2800.0                                     1.96  2011   
25               2785.0                                     1.95  2012   

    Median Year Structure Built  Median Year Moved In  \
24                       1939.0                2003.0   
25                       1939.0                2002.0   

    Percent with Bachelor's degree  Median rent burden  Evictions per units  \
24                            44.4                22.4             0.000357   
25                            42.2                24.9             0.000359   

    Percent Black  Percent White  Percent Asian 

31       0.010517       0.688431       0.242112         0.02213            0.0  
    Unnamed: 0       Geoid  num Evictions      geoid_year  Total Population  \
31          31  6075010900              1  60750109002011            4564.0   

    Total Housing Units  Total; Estimate; Average household size  Year  \
31               2932.0                                     1.74  2011   

    Median Year Structure Built  Median Year Moved In  \
31                       1939.0                2005.0   

    Percent with Bachelor's degree  Median rent burden  Evictions per units  \
31                            42.6                22.9             0.000341   

    Percent Black  Percent White  Percent Asian  Percent Native  Percent H, PI  
31       0.010517       0.688431       0.242112         0.02213            0.0  
    Unnamed: 0       Geoid  num Evictions      geoid_year  Total Population  \
31          31  6075010900              1  60750109002011            4564.0   

    Total Housin

...

Index: []
Empty DataFrame
Columns: [Unnamed: 0, Geoid, num Evictions, geoid_year, Total Population, Total Housing Units, Total; Estimate; Average household size, Year, Median Year Structure Built, Median Year Moved In, Percent with Bachelor's degree, Median rent burden, Evictions per units, Percent Black, Percent White, Percent Asian, Percent Native, Percent H, PI]
Index: []
Empty DataFrame
Columns: [Unnamed: 0, Geoid, num Evictions, geoid_year, Total Population, Total Housing Units, Total; Estimate; Average household size, Year, Median Year Structure Built, Median Year Moved In, Percent with Bachelor's degree, Median rent burden, Evictions per units, Percent Black, Percent White, Percent Asian, Percent Native, Percent H, PI]
Index: []
[0, 0, 0, 0, 0, 0, 0]
6075047600
60750476002013
2013
neighbor years: [2012, 2011]
     Unnamed: 0       Geoid  num Evictions      geoid_year  Total Population  \
773         773  6075047600              1  60750476002012            5508.0   

     Total 

     Unnamed: 0       Geoid  num Evictions      geoid_year  Total Population  \
787         787  6075047702              2  60750477022012            4152.0   

     Total Housing Units  Total; Estimate; Average household size  Year  \
787               1637.0                                     2.64  2012   

     Median Year Structure Built  Median Year Moved In  \
787                       1939.0                2004.0   

     Percent with Bachelor's degree  Median rent burden  Evictions per units  \
787                            34.3                26.4             0.001222   

     Percent Black  Percent White  Percent Asian  Percent Native  \
787       0.013487       0.413536       0.522158        0.001686   

     Percent H, PI  
787            0.0  
     Unnamed: 0       Geoid  num Evictions      geoid_year  Total Population  \
787         787  6075047702              2  60750477022012            4152.0   

     Total Housing Units  Total; Estimate; Average household size  Yea

60750478022017
2017
neighbor years: [2016, 2015]
     Unnamed: 0       Geoid  num Evictions      geoid_year  Total Population  \
801         801  6075047802              3  60750478022016            3937.0   

     Total Housing Units  Total; Estimate; Average household size  Year  \
801               1622.0                                     2.65  2016   

     Median Year Structure Built  Median Year Moved In  \
801                       1944.0                2010.0   

     Percent with Bachelor's degree  Median rent burden  Evictions per units  \
801                           820.0                27.5              0.00185   

     Percent Black  Percent White  Percent Asian  Percent Native  \
801            0.0       0.364999       0.542799        0.007112   

     Percent H, PI  
801        0.00254  
     Unnamed: 0       Geoid  num Evictions      geoid_year  Total Population  \
801         801  6075047802              3  60750478022016            3937.0   

     Total Housing Un

Empty DataFrame
Columns: [Unnamed: 0, Geoid, num Evictions, geoid_year, Total Population, Total Housing Units, Total; Estimate; Average household size, Year, Median Year Structure Built, Median Year Moved In, Percent with Bachelor's degree, Median rent burden, Evictions per units, Percent Black, Percent White, Percent Asian, Percent Native, Percent H, PI]
Index: []
Empty DataFrame
Columns: [Unnamed: 0, Geoid, num Evictions, geoid_year, Total Population, Total Housing Units, Total; Estimate; Average household size, Year, Median Year Structure Built, Median Year Moved In, Percent with Bachelor's degree, Median rent burden, Evictions per units, Percent Black, Percent White, Percent Asian, Percent Native, Percent H, PI]
Index: []
[0, 0, 0, 0, 0, 0]
6075061000
60750610002015
2015
neighbor years: [2014, 2013]
Empty DataFrame
Columns: [Unnamed: 0, Geoid, num Evictions, geoid_year, Total Population, Total Housing Units, Total; Estimate; Average household size, Year, Median Year Structure Built

Empty DataFrame
Columns: [Unnamed: 0, Geoid, num Evictions, geoid_year, Total Population, Total Housing Units, Total; Estimate; Average household size, Year, Median Year Structure Built, Median Year Moved In, Percent with Bachelor's degree, Median rent burden, Evictions per units, Percent Black, Percent White, Percent Asian, Percent Native, Percent H, PI]
Index: []
Empty DataFrame
Columns: [Unnamed: 0, Geoid, num Evictions, geoid_year, Total Population, Total Housing Units, Total; Estimate; Average household size, Year, Median Year Structure Built, Median Year Moved In, Percent with Bachelor's degree, Median rent burden, Evictions per units, Percent Black, Percent White, Percent Asian, Percent Native, Percent H, PI]
Index: []
Empty DataFrame
Columns: [Unnamed: 0, Geoid, num Evictions, geoid_year, Total Population, Total Housing Units, Total; Estimate; Average household size, Year, Median Year Structure Built, Median Year Moved In, Percent with Bachelor's degree, Median rent burden, Evi

In [293]:
features.to_csv("data/features_with_neighbor_means.csv")